In [1]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pathlib import Path
import plotly.io as pio
pio.templates

# set path to root directory
root = Path().cwd().parent
file_path = root / "data" / "PPA.xlsx"

# load excel file
xls = pd.ExcelFile(file_path)
xls.sheet_names

['Task Summary', 'PPA Data']

In [2]:
# Load the "PPA Data" sheet
ppa_data = pd.read_excel(xls, sheet_name="PPA Data")
df = ppa_data.copy()

# Display basic information and the first few rows
ppa_data.info(), ppa_data.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 105120 entries, 0 to 105119
Data columns (total 3 columns):
 #   Column                             Non-Null Count   Dtype         
---  ------                             --------------   -----         
 0   Date Time                          105120 non-null  datetime64[ns]
 1   Net Energy (Loss Factor Adjusted)  105120 non-null  float64       
 2   RRP                                105120 non-null  float64       
dtypes: datetime64[ns](1), float64(2)
memory usage: 2.4 MB


(None,
             Date Time  Net Energy (Loss Factor Adjusted)     RRP
 0 2023-01-01 00:05:00                                0.0  140.40
 1 2023-01-01 00:10:00                                0.0  133.96
 2 2023-01-01 00:15:00                                0.0  120.00
 3 2023-01-01 00:20:00                                0.0  118.99
 4 2023-01-01 00:25:00                                0.0  118.99)

In [3]:
# Summary statistics
ppa_data.describe()

Date Time  Net Energy (Loss Factor Adjusted)  \
count                         105120                      105120.000000   
mean   2023-07-02 12:02:30.000000256                           0.481839   
min              2023-01-01 00:05:00                           0.000000   
25%              2023-04-02 06:03:45                           0.000000   
50%              2023-07-02 12:02:30                           0.000000   
75%              2023-10-01 18:01:15                           0.792715   
max              2024-01-01 00:00:00                           2.776710   
std                              NaN                           0.736431   

                 RRP  
count  105120.000000  
mean       95.944268  
min      -999.990000  
25%        57.920000  
50%        85.980000  
75%       114.770000  
max     16599.890000  
std       294.875216

In [4]:
# Check date range
ppa_data["Date Time"].min(), ppa_data["Date Time"].max()


(Timestamp('2023-01-01 00:05:00'), Timestamp('2024-01-01 00:00:00'))

In [5]:
# Check for missing values
ppa_data.isnull().sum()

Date Time                            0
Net Energy (Loss Factor Adjusted)    0
RRP                                  0
dtype: int64

In [18]:
# Generate time features
df['Date Time'] = pd.to_datetime(df['Date Time'])
df['Quarter'] = df['Date Time'].dt.quarter
df['Month'] = df['Date Time'].dt.month
df['Hour'] = df['Date Time'].dt.hour
df['Year'] = df['Date Time'].dt.year
df['Date'] = df['Date Time'].dt.date

FLOOR_PRICE = 0
FIXED_RATE = 52.55

# Float Rate = MAX(RRP, Floor Price)
df['Float_Rate'] = df['RRP'].clip(lower=FLOOR_PRICE)

# Settlement = Net Energy × (Float Rate - Fixed Rate)
df['Settlement'] = df['Net Energy (Loss Factor Adjusted)'] * (df['Float_Rate'] - FIXED_RATE)

# Calculate cumulative P&L
df['Cumulative_PL'] = df['Settlement'].cumsum()

# Quarterly P&L summary
quarterly_pl = df.groupby('Quarter')['Settlement'].sum().round(2)
quarterly_stats = df.groupby('Quarter').agg({
    'RRP': ['mean', 'min', 'max'],
    'Net Energy (Loss Factor Adjusted)': 'sum',
    'Settlement': 'sum'
}).round(2)

# Print quarterly P&L
print("\nQuarterly P&L Summary:")
print(quarterly_pl)

df


Quarterly P&L Summary:
Quarter
1    211529.70
2    166488.88
3   -241343.71
4   -163428.16
Name: Settlement, dtype: float64


Date Time  Net Energy (Loss Factor Adjusted)     RRP  \
0      2023-01-01 00:05:00                                0.0  140.40   
1      2023-01-01 00:10:00                                0.0  133.96   
2      2023-01-01 00:15:00                                0.0  120.00   
3      2023-01-01 00:20:00                                0.0  118.99   
4      2023-01-01 00:25:00                                0.0  118.99   
...                    ...                                ...     ...   
105115 2023-12-31 23:40:00                                0.0   57.98   
105116 2023-12-31 23:45:00                                0.0   57.98   
105117 2023-12-31 23:50:00                                0.0   57.98   
105118 2023-12-31 23:55:00                                0.0   57.98   
105119 2024-01-01 00:00:00                                0.0   57.98   

        Quarter  Month  Hour  Year        Date  Float_Rate  Settlement  \
0             1      1     0  2023  2023-01-01      140.40         0.0   
1             1      1     0  2023  2023-01-01      133.96         0.0   
2             1      1     0  2023  2023-01-01      120.00         0.0   
3             1      1     0  2023  2023-01-01      118.99         0.0   
4             1      1     0  2023  2023-01-01      118.99         0.0   
...         ...    ...   ...   ...         ...         ...         ...   
105115        4     12    23  2023  2023-12-31       57.98         0.0   
105116        4     12    23  2023  2023-12-31       57.98         0.0   
105117        4     12    23  2023  2023-12-31       57.98         0.0   
105118        4     12    23  2023  2023-12-31       57.98         0.0   
105119        1      1     0  2024  2024-01-01       57.98         0.0   

        Cumulative_PL  
0            0.000000  
1            0.000000  
2            0.000000  
3            0.000000  
4            0.000000  
...               ...  
105115  -26753.292532  
105116  -26753.292532  
105117  -26753.292532  
105118  -26753.292532  
105119  -26753.292532  

[105120 rows x 11 columns]

In [37]:
import plotly.io as pio
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Set the theme
pio.templates.default = "plotly"

# Quarterly P&L summary
quarterly_pl = df.groupby('Quarter')['Settlement'].sum().round(2)
quarterly_stats = df.groupby('Quarter').agg({
    'RRP': ['mean', 'min', 'max'],
    'Net Energy (Loss Factor Adjusted)': 'sum',
    'Settlement': 'sum'
}).round(2)

# Create the dashboard
fig = make_subplots(
    rows=5, cols=2,
    subplot_titles=(
        'Quarterly P&L Summary',
        'Daily Energy Volume and RRP Trends',
        'Regional Reference Price Distribution', 'Average Price by Hour',
        'Quarterly P&L', 'Cumulative P&L Over Time',
        'Key Metrics Summary',
    ),
    specs=[
        [{"type": "table", "colspan": 2}, None],
        [{"type": "xy", "secondary_y": True, "colspan": 2}, None],
        [{"type": "histogram"}, {"type": "scatter"}],
        [{"type": "bar"}, {"type": "scatter"}],
        [{"type": "table", "colspan": 2}, None]
    ],
    vertical_spacing=0.05,
    horizontal_spacing=0.08,
    row_heights=[0.12, 0.25, 0.25, 0.25, 0.15]
)

# 1. Quarterly P&L Table
fig.add_trace(
    go.Table(
        header=dict(values=['Quarter', 'Avg RRP ($/MWh)', 'Min RRP', 'Max RRP', 'Total Energy (MWh)', 'Total P&L ($)']),
        cells=dict(values=[
            quarterly_stats.index.astype(str),
            quarterly_stats[('RRP', 'mean')],
            quarterly_stats[('RRP', 'min')],
            quarterly_stats[('RRP', 'max')],
            quarterly_stats[('Net Energy (Loss Factor Adjusted)', 'sum')],
            quarterly_stats[('Settlement', 'sum')]
        ])
    ),
    row=1, col=1
)

# 2. Daily Volume and RRP Trends
daily_stats = df.groupby('Date').agg({
    'Net Energy (Loss Factor Adjusted)': 'sum',
    'RRP': 'mean'
}).reset_index()

fig.add_trace(
    go.Scatter(
        x=daily_stats['Date'],
        y=daily_stats['Net Energy (Loss Factor Adjusted)'],
        mode='lines',
        name='Daily Energy Volume'
    ),
    row=2, col=1, secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=daily_stats['Date'],
        y=daily_stats['RRP'],
        mode='lines',
        name='Average Daily RRP'
    ),
    row=2, col=1, secondary_y=True
)

# 3. Price Distribution
fig.add_trace(
    go.Histogram(
        x=df['RRP'],
        nbinsx=50,
        name='RRP Distribution'
    ),
    row=3, col=1
)

# 4. Average Hourly Price
hourly_price = df.groupby('Hour')['RRP'].mean().reset_index()
fig.add_trace(
    go.Scatter(
        x=hourly_price['Hour'],
        y=hourly_price['RRP'],
        mode='lines+markers',
        name='Avg Hourly Price'
    ),
    row=3, col=2
)

# 5. Quarterly P&L
fig.add_trace(
    go.Bar(
        x=[f'Q{q}' for q in quarterly_pl.index],
        y=quarterly_pl.values,
        name='Quarterly P&L'
    ),
    row=4, col=1
)

# 6. Cumulative P&L
fig.add_trace(
    go.Scatter(
        x=df['Date Time'],
        y=df['Cumulative_PL'],
        mode='lines',
        name='Cumulative P&L'
    ),
    row=4, col=2
)

# Calculate key metrics
def calculate_key_metrics(df):
    # Calculate RRP mean and standard deviation
    rrp_mean = df['RRP'].mean()
    rrp_std = df['RRP'].std()
    
    # Define outlier thresholds (3 standard deviations)
    high_price_threshold = rrp_mean + (3 * rrp_std)
    low_price_threshold = rrp_mean - (3 * rrp_std)
    
    metrics = {
        'Price_Analysis': {
            'Time_Weighted_Average': rrp_mean,
            'Volume_Weighted_Average': (df['RRP'] * df['Net Energy (Loss Factor Adjusted)']).sum() / df['Net Energy (Loss Factor Adjusted)'].sum(),
            'Price_Volatility': rrp_std
        },
        'Market_Events': {
            'High_Price_Events': len(df[df['RRP'] > high_price_threshold]),
            'Low_Price_Events': len(df[df['RRP'] < low_price_threshold]),
            'Negative_Price_Events': len(df[df['RRP'] < 0])
        }
    }
    return metrics

metrics = calculate_key_metrics(df)

# 7. Key Metrics Table
fig.add_trace(
    go.Table(
        header=dict(values=['Metric', 'Value']),
        cells=dict(values=[
            ['Time Weighted Avg Price', 'Volume Weighted Avg Price', 'Price Volatility (Standard Deviations)', 'High Price Events', 'Low_Price_Events', 'Negative Price Events'],
            [
                f"{metrics['Price_Analysis']['Time_Weighted_Average']:.2f}",
                f"{metrics['Price_Analysis']['Volume_Weighted_Average']:.2f}",
                f"{metrics['Price_Analysis']['Price_Volatility']:.2f}",
                metrics['Market_Events']['High_Price_Events'],
                metrics['Market_Events']['Low_Price_Events'],
                metrics['Market_Events']['Negative_Price_Events']
            ]
        ])
    ),
    row=5, col=1
)

# Formatting
fig.update_layout(
    height=1600,
    title_text="PPA Analysis Dashboard",
    title_x=0.5,
    title_font_size=24,
    showlegend=True,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        xanchor="center",
        x=0.5
    ),
    autosize=True,
    margin=dict(l=50, r=50, t=100, b=50)
)

# Update axes labels
fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_yaxes(title_text="Volume (MWh)", secondary_y=False, row=2, col=1)
fig.update_yaxes(title_text="RRP ($/MWh)", secondary_y=True, row=2, col=1)

fig.update_xaxes(title_text="Price ($/MWh)", row=3, col=1)
fig.update_yaxes(title_text="Frequency", row=3, col=1)

fig.update_xaxes(title_text="Hour of Day", row=3, col=2)
fig.update_yaxes(title_text="Average Price ($/MWh)", row=3, col=2)

fig.update_xaxes(title_text="Quarter", row=4, col=1)
fig.update_yaxes(title_text="P&L ($)", row=4, col=1)

fig.update_xaxes(title_text="Date", row=4, col=2)
fig.update_yaxes(title_text="Cumulative P&L ($)", row=4, col=2)


fig.show()

# Save dashboard to html
fig.write_html(
    root / "dashboard.html", 
    config={
        'responsive': True,
        'displayModeBar': True,
        'displaylogo': False,
    },
    full_html=True,
    include_plotlyjs=True
)